In [1]:
%load_ext autoreload
%autoreload 2

%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
from PIL import Image
import torch
from importlib.util import find_spec
if find_spec("text_recognizer") is None:
    import sys
    sys.path.append('..')

In [4]:
from text_recognizer.networks.residual_network import IdentityBlock, ResidualBlock, BasicBlock, BottleNeckBlock, ResidualLayer, ResidualNetwork

In [5]:
IdentityBlock(32, 64)

IdentityBlock(
  (blocks): Identity()
  (activation_fn): ReLU(inplace=True)
  (shortcut): Identity()
)

In [6]:
ResidualBlock(32, 64)

ResidualBlock(
  (blocks): Identity()
  (activation_fn): ReLU(inplace=True)
  (shortcut): Sequential(
    (0): Conv2d(32, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
)

In [7]:
dummy = torch.ones((1, 32, 224, 224))

block = BasicBlock(32, 64)
block(dummy).shape
print(block)

BasicBlock(
  (blocks): Sequential(
    (0): Sequential(
      (0): Conv2dAuto(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): ReLU(inplace=True)
    (2): Sequential(
      (0): Conv2dAuto(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
  )
  (activation_fn): ReLU(inplace=True)
  (shortcut): Sequential(
    (0): Conv2d(32, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
)


In [8]:
dummy = torch.ones((1, 32, 10, 10))

block = BottleNeckBlock(32, 64)
block(dummy).shape
print(block)

BottleNeckBlock(
  (blocks): Sequential(
    (0): Sequential(
      (0): Conv2dAuto(32, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): ReLU(inplace=True)
    (2): Sequential(
      (0): Conv2dAuto(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (3): ReLU(inplace=True)
    (4): Sequential(
      (0): Conv2dAuto(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
  )
  (activation_fn): ReLU(inplace=True)
  (shortcut): Sequential(
    (0): Conv2d(32, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
)


In [ ]:
dummy = torch.ones((1, 64, 48, 48))

layer = ResidualLayer(64, 128, block=BasicBlock, num_blocks=3)
layer(dummy).shape

In [ ]:
blocks_sizes=[64, 128, 256, 512]
list(zip(blocks_sizes, blocks_sizes[1:]))

In [69]:
e = Encoder(depths=[2, 1], block_sizes= [96, 128])

In [75]:
Encoder(**{"depths": [2, 1], "block_sizes": [96, 128]})

Encoder(
  (gate): Sequential(
    (0): Conv2d(1, 96, kernel_size=(3, 3), stride=(2, 2), padding=(3, 3), bias=False)
    (1): BatchNorm2d(96, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): ReLU(inplace=True)
    (3): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  )
  (blocks): Sequential(
    (0): ResidualLayer(
      (blocks): Sequential(
        (0): BasicBlock(
          (blocks): Sequential(
            (0): Sequential(
              (0): Conv2dAuto(96, 96, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
              (1): BatchNorm2d(96, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            )
            (1): ReLU(inplace=True)
            (2): Sequential(
              (0): Conv2dAuto(96, 96, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
              (1): BatchNorm2d(96, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            )
          )
          (

In [9]:
from text_recognizer.networks import WideResidualNetwork

In [10]:
wr = WideResidualNetwork(
            in_channels= 1,
            num_classes= 80,
            depth= 16,
            num_layers= 4,
            width_factor= 2,
            dropout_rate= 0.2,
            activation= "SELU",
            use_decoder= False,
)

In [11]:
from torchsummary import summary

In [14]:
summary(wr, (1, 28, 14), device="cpu", depth=10)

Layer (type:depth-idx)                        Output Shape              Param #
├─Sequential: 1-1                             [-1, 256, 4, 2]           --
|    └─Conv2d: 2-1                            [-1, 16, 28, 14]          144
|    └─Sequential: 2-2                        [-1, 32, 28, 14]          --
|    |    └─WideBlock: 3-1                    [-1, 32, 28, 14]          --
|    |    |    └─Sequential: 4-1              [-1, 32, 28, 14]          --
|    |    |    |    └─Conv2d: 5-1             [-1, 32, 28, 14]          512
|    |    |    └─Sequential: 4-2              [-1, 32, 28, 14]          --
|    |    |    |    └─BatchNorm2d: 5-2        [-1, 16, 28, 14]          32
|    |    |    └─SELU: 4-3                    [-1, 16, 28, 14]          --
|    |    |    └─Sequential: 4                []                        --
|    |    |    |    └─SELU: 5-3               [-1, 16, 28, 14]          --
|    |    |    |    └─Conv2d: 5-4             [-1, 32, 28, 14]          4,608
|    |    |    

Layer (type:depth-idx)                        Output Shape              Param #
├─Sequential: 1-1                             [-1, 256, 4, 2]           --
|    └─Conv2d: 2-1                            [-1, 16, 28, 14]          144
|    └─Sequential: 2-2                        [-1, 32, 28, 14]          --
|    |    └─WideBlock: 3-1                    [-1, 32, 28, 14]          --
|    |    |    └─Sequential: 4-1              [-1, 32, 28, 14]          --
|    |    |    |    └─Conv2d: 5-1             [-1, 32, 28, 14]          512
|    |    |    └─Sequential: 4-2              [-1, 32, 28, 14]          --
|    |    |    |    └─BatchNorm2d: 5-2        [-1, 16, 28, 14]          32
|    |    |    └─SELU: 4-3                    [-1, 16, 28, 14]          --
|    |    |    └─Sequential: 4                []                        --
|    |    |    |    └─SELU: 5-3               [-1, 16, 28, 14]          --
|    |    |    |    └─Conv2d: 5-4             [-1, 32, 28, 14]          4,608
|    |    |    